In [1]:
from rl_env_sarl import SARLDraftEnv
import gymnasium as gym
from stable_baselines3 import DQN
from stable_baselines3.common.env_checker import check_env

/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [2]:
dqn_params = {
    'policy': 'MlpPolicy',
    'policy_kwargs': dict(net_arch=[128, 128]),
    'learning_rate': 3e-4,
    'buffer_size': 10000,
    'learning_starts': 1000,
    'batch_size': 128,
    'tau': 5e-3,
    'gamma': 0.99,
    'train_freq': 4,
    'gradient_steps': 1,
    'target_update_interval': 1, # the default is much higher but i think since tau is so low it's okay
    'exploration_fraction': 0.1,
    'exploration_initial_eps': 1.0,
    # 'exploration_initial_eps': 0.05,
    'exploration_final_eps': 0.05,
    'max_grad_norm': 10,  # much more conservative than what i did before
    'verbose': 1,
    'stats_window_size': 100
}

In [3]:
check_env(SARLDraftEnv())

In [4]:
# env = SARLDraftEnv()
# model = DQN(env=env, **dqn_params)
# model.learn(total_timesteps=100000)

In [5]:
import os
import json
import numpy as np
from datetime import datetime
from stable_baselines3 import DQN
from stable_baselines3.common.callbacks import BaseCallback, CheckpointCallback, EvalCallback
from stable_baselines3.common.logger import configure

# Custom callback for monitoring and saving during training
class TrainingMonitorCallback(BaseCallback):
    def __init__(self, log_interval: int, save_interval: int, draft_save_interval: int, log_dir: str, run_id: str, verbose=1):
        super(TrainingMonitorCallback, self).__init__(verbose)
        self.log_interval = log_interval
        self.save_interval = save_interval
        self.draft_save_interval = draft_save_interval
        self.log_dir = log_dir
        self.run_id = run_id
        self.best_mean_reward = -np.inf
        self.rewards_history = []
        self.losses_history = []
        self.draft_history = []
        self.episode_counter = 0

        self.model_save_path = os.path.join(log_dir, f'best_model_{run_id}')
        self.rewards_losses_path = os.path.join(log_dir, f'rewards_losses_{run_id}.json')
        self.drafts_save_path = os.path.join(log_dir, f'draft_history_{run_id}.json')

    def _init_callback(self) -> None:
        os.makedirs(self.log_dir, exist_ok=True)

    def _on_step(self) -> bool:
        # Log rewards
        current_reward = self.locals['rewards']
        self.rewards_history.append(current_reward)

        # Log losses if TD errors are available
        if 'td_errors' in self.locals:
            current_loss = np.mean(np.abs(self.locals['td_errors']))
            self.losses_history.append(current_loss)

        # Periodic logging and saving
        if self.n_calls % self.log_interval == 0:
            mean_reward = np.mean(self.rewards_history[-self.log_interval:])
            self.logger.record('mean_reward', mean_reward)

            if mean_reward > self.best_mean_reward:
                self.best_mean_reward = mean_reward
                self.model.save(self.model_save_path)
                if self.verbose > 0:
                    print(f"New best mean reward: {self.best_mean_reward}. Model saved to {self.model_save_path}")

            # Convert rewards and losses to lists before saving
            rewards_list = [float(reward) for reward in self.rewards_history]
            losses_list = [float(loss) for loss in self.losses_history]

            # Save rewards and losses to a file
            with open(self.rewards_losses_path, 'w') as f:
                json.dump({'rewards': rewards_list, 'losses': losses_list}, f)

        # Check if the episode has terminated
        if self.locals['dones'][0]:
            
            if self.episode_counter % self.draft_save_interval == 0:
                draft = self.locals['infos'][0]['draft']
                self.draft_history.append(draft)
                with open(self.drafts_save_path, 'w') as f:
                    json.dump(self.draft_history, f, indent=4)
                
            self.episode_counter += 1

        return True

# Define your environment
env = SARLDraftEnv()

# Generate a unique run ID
run_id = datetime.now().strftime("%Y%m%d-%H%M%S")

# Choose significant parameters to include in the log directory name
param_str = f"DQN_lr_{dqn_params['learning_rate']}_gamma_{dqn_params['gamma']}"
log_dir = f"./logs/{param_str}_{run_id}/"
os.makedirs(log_dir, exist_ok=True)

# Save dqn_params to a JSON file
params_save_path = os.path.join(log_dir, f'dqn_params_{run_id}.json')
with open(params_save_path, 'w') as f:
    json.dump(dqn_params, f, indent=4)

# Configure the logger
new_logger = configure(log_dir, ["stdout", "csv", "tensorboard"])

# # Reload the model from a saved checkpoint
# model_path = 'logs/DQN_lr_0.001_gamma_0.99_20240826-133826/best_model.zip'
# model = DQN.load(model_path, env=env, tensorboard_log=log_dir)
# model.set_logger(new_logger)

# Define the model and attach the logger
model = DQN(env=env, **dqn_params, tensorboard_log=log_dir)
model.set_logger(new_logger)


# Log dqn_params to TensorBoard/CSV
for key, value in dqn_params.items():
    model.logger.record(f'params/{key}', value)

# Initialize and use the custom callback
monitor_callback = TrainingMonitorCallback(log_interval=1000, save_interval=50, draft_save_interval=1000, log_dir=log_dir, run_id=run_id)

# Create a checkpoint callback to save the model periodically
checkpoint_callback = CheckpointCallback(save_freq=1000, save_path=log_dir, name_prefix='rl_model')

# Create an evaluation callback to log evaluations during training
eval_callback = EvalCallback(env, best_model_save_path=log_dir, log_path=log_dir, eval_freq=5000, deterministic=True, render=False)

# Combine all callbacks
callback = [checkpoint_callback, eval_callback, monitor_callback]

# Train the model
model.learn(total_timesteps=5e5, callback=callback)

Logging to ./logs/DQN_lr_0.0003_gamma_0.99_20240826-200734/
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
---------------------------------------------------------
| params/                    |                          |
|    batch_size              | 128                      |
|    buffer_size             | 10000                    |
|    exploration_final_eps   | 0.05                     |
|    exploration_fraction    | 0.1                      |
|    exploration_initial_eps | 1                        |
|    gamma                   | 0.99                     |
|    gradient_steps          | 1                        |
|    learning_rate           | 0.0003                   |
|    learning_starts         | 1000                     |
|    max_grad_norm           | 10                       |
|    policy                  | MlpPolicy                |
|    policy_kwargs           | {'net_arch': [128, 128]} |
|    stats_window_size       | 100

/var/folders/st/_8t9rcwd49jf2y161kkqlch40000gn/T/ipykernel_64187/3244701906.py:53: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  rewards_list = [float(reward) for reward in self.rewards_history]


-------------------------------------
| mean_reward         | -0.03517894 |
| rollout/            |             |
|    ep_len_mean      | 15          |
|    ep_rew_mean      | -0.543      |
|    exploration_rate | 0.981       |
| time/               |             |
|    episodes         | 68          |
|    fps              | 14          |
|    time_elapsed     | 70          |
|    total_timesteps  | 1020        |
| train/              |             |
|    learning_rate    | 0.0003      |
|    loss             | 0.0321      |
|    n_updates        | 4           |
-------------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 15       |
|    ep_rew_mean      | -0.554   |
|    exploration_rate | 0.979    |
| time/               |          |
|    episodes         | 72       |
|    fps              | 14       |
|    time_elapsed     | 74       |
|    total_timesteps  | 1080     |
| train/              |          |
|    le

/var/folders/st/_8t9rcwd49jf2y161kkqlch40000gn/T/ipykernel_64187/3244701906.py:53: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  rewards_list = [float(reward) for reward in self.rewards_history]


--------------------------------------
| mean_reward         | -0.036475558 |
| rollout/            |              |
|    ep_len_mean      | 15           |
|    ep_rew_mean      | -0.546       |
|    exploration_rate | 0.961        |
| time/               |              |
|    episodes         | 136          |
|    fps              | 14           |
|    time_elapsed     | 141          |
|    total_timesteps  | 2040         |
| train/              |              |
|    learning_rate    | 0.0003       |
|    loss             | 0.0051       |
|    n_updates        | 259          |
--------------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 15       |
|    ep_rew_mean      | -0.519   |
|    exploration_rate | 0.96     |
| time/               |          |
|    episodes         | 140      |
|    fps              | 14       |
|    time_elapsed     | 145      |
|    total_timesteps  | 2100     |
| train/              |   

...

/var/folders/st/_8t9rcwd49jf2y161kkqlch40000gn/T/ipykernel_64187/3244701906.py:53: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  rewards_list = [float(reward) for reward in self.rewards_history]


------------------------------------
| mean_reward         | 0.05363181 |
| rollout/            |            |
|    ep_len_mean      | 15         |
|    ep_rew_mean      | 0.806      |
|    exploration_rate | 0.05       |
| time/               |            |
|    episodes         | 33236      |
|    fps              | 14         |
|    time_elapsed     | 34437      |
|    total_timesteps  | 499035     |
| train/              |            |
|    learning_rate    | 0.0003     |
|    loss             | 0.000303   |
|    n_updates        | 124508     |
------------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 15       |
|    ep_rew_mean      | 0.806    |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 33240    |
|    fps              | 14       |
|    time_elapsed     | 34441    |
|    total_timesteps  | 499095   |
| train/              |          |
|    learning_rate    |

/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=500000, episode_reward=0.80 +/- 0.03
Episode length: 15.00 +/- 0.00
----------------------------------
| eval/               |          |
|    mean_ep_length   | 15       |
|    mean_reward      | 0.798    |
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    total_timesteps  | 500000   |
| train/              |          |
|    learning_rate    | 0.0003   |
|    loss             | 3.55e-05 |
|    n_updates        | 124749   |
----------------------------------


/var/folders/st/_8t9rcwd49jf2y161kkqlch40000gn/T/ipykernel_64187/3244701906.py:53: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  rewards_list = [float(reward) for reward in self.rewards_history]
